![Wedding Problem](Problem.png)

In [ ]:
import pandas as pd

# Show all rows and columns
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

# If needed, also expand the width
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)  # or a large int

from copy import deepcopy
from random import randint, choice
import random

from library.solution import Solution
from library.algorithms.hill_climbing import hill_climbing
from library.algorithms.simulated_annealing import simulated_annealing

![Guests](guests.png)

In [3]:
df = pd.read_csv("seating_data.csv")
df

idx     1     2     3     4    5    6     7     8    9   10    11    12  \
0     1     0  5000     0     0  700  700     0     0    0    0     0     0   
1     2  5000     0   700   700    0    0   300   300  500  500   300   300   
2     3     0   700     0  2000    0    0     0     0  300  300   900     0   
3     4     0   700  2000     0    0    0   900   400  300  300     0     0   
4     5   700     0     0     0    0    0     0     0    0    0     0     0   
5     6   700     0     0     0    0    0     0     0    0    0     0     0   
6     7     0   300     0   900    0    0     0  2000  700  700     0     0   
7     8     0   300     0   400    0    0  2000     0  700  700     0     0   
8     9     0   500   300   300    0    0   700   700    0    0     0     0   
9    10     0   500   300   300    0    0   700   700    0    0     0     0   
10   11     0   300   900     0    0    0     0     0    0    0     0  2000   
11   12     0   300     0     0    0    0     0     0    0    0  2000     0   
12   13     0   300   900     0    0    0     0     0    0    0   900     0   
13   14     0   300     0     0    0    0     0     0    0    0     0     0   
14   15     0   500   300   300    0    0     0     0    0    0   300     0   
15   16   900     0     0     0  700  900     0     0    0    0     0     0   
16   17   900     0     0     0  700  900     0     0    0    0     0     0   
17   18   900     0     0     0  700  900     0     0    0    0     0     0   
18   19   300     0     0     0  400  400     0     0    0    0     0     0   
19   20   300     0     0     0  400  400     0     0    0    0     0     0   
20   21   300     0     0     0  400  400     0     0    0    0     0     0   
21   22     0     0     0     0    0    0     0     0    0    0     0     0   
22   23   500     0     0     0  300  300     0     0    0    0     0     0   
23   24   300     0     0     0  900  400     0     0    0    0     0     0   
24   25   300     0     0     0  400    0     0     0    0    0     0     0   
25   26   300     0     0     0    0  400     0     0    0    0     0     0   
26   27   300     0     0     0  400  900     0     0    0    0     0     0   
27   28   500     0     0     0  300  300     0     0    0    0     0     0   
28   29   100   100     0     0    0    0     0     0    0    0     0     0   
29   30   100   100     0     0    0    0     0     0    0    0     0     0   
30   31     0     0     0     0    0    0     0     0    0    0     0     0   
31   32     0   100     0     0    0    0     0     0    0    0     0     0   
32   33     0     0     0     0    0    0     0     0    0    0     0     0   
33   34     0   100     0     0    0    0     0     0    0    0     0     0   
34   35     0   100     0     0    0    0     0     0    0    0     0     0   
35   36     0   100     0     0    0    0     0     0    0    0     0     0   
36   37   100     0     0     0    0    0     0     0    0    0     0     0   
37   38  1000     0     0     0    0    0     0     0    0    0     0     0   
38   39     0   100     0     0    0    0     0     0    0    0     0     0   
39   40   100   100     0     0    0    0     0     0    0    0     0     0   
40   41   100   100     0     0    0    0     0     0    0    0     0     0   
41   42     0     0     0     0    0    0     0     0    0    0     0     0   
42   43     0     0     0     0    0    0     0     0    0    0     0     0   
43   44   100     0     0     0    0    0     0     0    0    0     0     0   
44   45     0   100     0     0    0    0     0     0    0    0     0     0   
45   46   100   100     0     0    0    0     0     0    0    0     0     0   
46   47   100   100     0     0    0    0     0     0    0    0     0     0   
47   48     0     0     0     0    0    0     0     0  100  100     0     0   
48   49   100   100     0     0    0    0     0     0    0    0     0     0   
49   50  1000     0     0     0    0    0     0     0 

0 - 64 elements - represent the rows
fitness = df[index][neighbor] --> df[df['idx'] == 1]['1']

In [4]:
class SeatingSolution(Solution):
    def __init__(self, repr=None):
        super().__init__(repr=repr)

    # Override the superclass's methods
    def random_initial_representation(self):
        tables = {1: [], 2: [], 3: [], 4:[], 5:[], 6:[], 7:[], 8:[]}
        attendees = list(range(1,65))
        random.shuffle(attendees)

        table = 1
        while len(attendees) > 0:
            tables[table].append(attendees.pop())
            if len(tables[table]) == 8:
                table += 1
                
        return tables


    def fitness(self):
        fitness = 0
        for i in range(1,8): # loop through the tables
            keys = self.repr[i]
            keys_seen = []
            for indexes in keys: # loop through the keys and find the fitness per the df
                for key in keys:
                    if key not in keys_seen: # skip the keys that were already counted to not count them twice
                        fitness += df[df['idx'] == indexes][str(key)].values[0] 
                keys_seen.append(indexes)
        return fitness

In [ ]:
# Intialize with representation
initialized_solution = {1: [1, 2, 6, 19, 32, 34, 36, 39], 2: [10, 13, 14, 25, 28, 44, 49, 56], 3: [11, 12, 17, 18, 30, 41, 47, 48], 4: [5, 20, 24, 29, 37, 51, 55], 5: [9, 15, 38, 42, 54, 57], 6: [3, 7, 8, 23, 27, 31, 43, 50], 7: [21, 35, 40, 53], 8: [4, 16, 22, 26, 33, 52, 58, 59]}
solution = SeatingSolution(initialized_solution)

# Initialize with random representation
solution_random = SeatingSolution()

print(f'Solution {solution}\nFitness: {solution.fitness()}\n')
print(f'Random solution {solution_random}\nFitness: {solution_random.fitness()}')

In [ ]:
class Seating_RandomSwapNeighborhood_HillClimbingSolution(SeatingSolution):

    # This method must return a list of IntBin_IntNeighborhood_HillClimbingSolution objects (the neighbors)
    def get_neighbors(self):
        # this method swaps 2 random people from 2 random tables
        neighbors = []
        swaps = 64

        while swaps >= 0:
            randomTableA, randomTableB = randint(1, 8), randint(1, 8)
            while randomTableB == randomTableA:
                randomTableB = randint(1, 8)

            # randomly select someone from the randomly chosen tables
            randomPersonA = choice(self.repr[randomTableA])
            randomPersonB = choice(self.repr[randomTableB])

            # Swap the two people between the tables
            seatingNeighbor = deepcopy(self.repr)
            seatingNeighbor[randomTableA].remove(randomPersonA)
            seatingNeighbor[randomTableB].remove(randomPersonB)
            seatingNeighbor[randomTableA].append(randomPersonB)
            seatingNeighbor[randomTableB].append(randomPersonA)

            neighbors.append(
                Seating_RandomSwapNeighborhood_HillClimbingSolution(repr=seatingNeighbor)
            )
            swaps -= 1


        return neighbors

In [ ]:
# need a way to customize the number of tables
# need a way to customize the number of ppl being assigned to tables
# need a mock way of adding value to custom seating

In [ ]:
# Initialize random solution
solution = Seating_RandomSwapNeighborhood_HillClimbingSolution()
print('Solution', solution)

neighbors = solution.get_neighbors()
print('Neighbors:')
for neighbor in neighbors:
    print(neighbor)

In [ ]:
initial_solution = Seating_RandomSwapNeighborhood_HillClimbingSolution()
best_solution = hill_climbing(initial_solution, maximization=True, verbose=True, max_iter=100)

print('Best solution', best_solution)

> Noticed that when using a single random swap per neighbor there isn't much improvement in fitness scores when using Hill Climbing - theory is that the fitness landscape is prodominetly zeros.

In [ ]:
class Seating_SingleGreedyNeighborhood_HillClimbingSolution(SeatingSolution):

    def _get_current_table(self, person):
        for table, guests in self.repr.items():
            if person in guests:
                return table
        return None  # if not found
    
    # This method must return a list of Solution objects (the neighbors)
    def get_neighbors(self):
        # this method swaps 2 random people from 2 random tables
        neighbors = []
        # swaps = 64
        randomTableA = randint(1, 8)
        personAIndex = randint(0, len(self.repr[randomTableA])-1 )
        personA = self.repr[randomTableA][personAIndex]

        # get only the people that the randomly chosen person has a relationship with
        filtered = df[df['idx'] == personA].iloc[0]
        filtered = filtered.drop('idx')
        peopleWithRelationship = [int(x) for x in filtered[filtered != 0].index] # convert to a list of numbers instead of strings like the Series would give

        for personB in peopleWithRelationship: 
            tableB = self._get_current_table(personB)

            if tableB == randomTableA:
                continue
            
            # add the randomly chosen person to the new table
            seatingNeighbor = deepcopy(self.repr)
            seatingNeighbor[randomTableA].append(personB)
            seatingNeighbor[tableB].append(personA)

            # remove the original ppl seated at the table
            seatingNeighbor[randomTableA].remove(personA)
            seatingNeighbor[tableB].remove(personB)

            neighbors.append(Seating_SingleGreedyNeighborhood_HillClimbingSolution(repr=seatingNeighbor))

        return neighbors

In [ ]:
# Initialize random solution
solution = Seating_SingleGreedyNeighborhood_HillClimbingSolution()
print('Solution', solution)

In [ ]:
neighbors = solution.get_neighbors()
print('Neighbors:')
for neighbor in neighbors:
    print(neighbor)

In [ ]:
initial_solution = Seating_SingleGreedyNeighborhood_HillClimbingSolution()
best_solution = hill_climbing(initial_solution, maximization=True, verbose=True, max_iter=100)

print('Best solution', best_solution)

In [ ]:
class Seating_MultipleGreedyNeighborhood_HillClimbingSolution(SeatingSolution):

    def _get_current_table(self, person):
        for table, guests in self.repr.items():
            if person in guests:
                return table
        return None  # if not found
    
    def get_neighbors(self):
        neighbors = []

        # Iterate over all tables
        for _ in range(64):  # You can choose to run 64 swaps per iteration
            randomTableA = randint(1, 8)
            personAIndex = randint(0, len(self.repr[randomTableA]) - 1)
            personA = self.repr[randomTableA][personAIndex]

            # Get the people this person has a relationship with
            filtered = df[df['idx'] == personA].iloc[0]
            filtered = filtered.drop('idx')
            peopleWithRelationship = [int(x) for x in filtered[filtered != 0].index] 

            for personB in peopleWithRelationship:
                tableB = self._get_current_table(personB)

                if tableB == randomTableA:
                    continue

                # Create a new seating arrangement (swap personA and personB)
                seatingNeighbor = deepcopy(self.repr)

                # Perform the swap: move personA to tableB, and personB to tableA
                seatingNeighbor[randomTableA].append(personB)
                seatingNeighbor[tableB].append(personA)

                # Remove the original people from their original tables
                seatingNeighbor[randomTableA].remove(personA)
                seatingNeighbor[tableB].remove(personB)

                # Add the new neighbor to the list
                neighbors.append(Seating_MultipleGreedyNeighborhood_HillClimbingSolution(repr=seatingNeighbor))

        return neighbors

In [ ]:
# Initialize random solution
solution = Seating_MultipleGreedyNeighborhood_HillClimbingSolution()
print('Solution', solution)

neighbors = solution.get_neighbors()
print('Neighbors:')
for neighbor in neighbors:
    print(neighbor)

In [ ]:
initial_solution = Seating_MultipleGreedyNeighborhood_HillClimbingSolution()
best_solution = hill_climbing(initial_solution, maximization=True, verbose=True, max_iter=100)

print('Best solution', best_solution)

In [ ]:
# took an hour to run all 10 solutions
fitnesses = []
for _ in range(10):
    initial_solution = Seating_MultipleGreedyNeighborhood_HillClimbingSolution()
    best_solution = hill_climbing(initial_solution, maximization=True, verbose=False)
    fitnesses.append(best_solution.fitness())

In [ ]:
fitnesses

In [ ]:
fitnesses = [41600, 45700, 37700, 37700, 39100, 36500, 34000, 34600, 35600, 37900]
avg_fitness = sum(fitnesses) / len(fitnesses)
print("Descriptions of the fitness for the multiple greedy hill climbing solution: ")
print("Average: ", int(avg_fitness))
print("Max: \t ", max(fitnesses))
print("Min: \t ", min(fitnesses))

---

### Simulated Annealing

In [5]:
class Seating_RandomSwapNeighborhood_SA_Solution(SeatingSolution):

    # This method must return a list of IntBin_IntNeighborhood_HillClimbingSolution objects (the neighbors)
    def get_random_neighbor(self):
        # this method swaps 2 random people from 2 random tables
        # neighbors = []
        # swaps = 64

        # while swaps >= 0:
        randomTableA = randint(1, 8)    
        randomTableB = randint(1, 8)
        while randomTableB != randomTableA:
            randomTableB = randint(1, 8)
        
        # get number of ppl sitting at the table
        personAIndex = randint(0, len(self.repr[randomTableA])-1 )
        personBIndex = randint(0, len(self.repr[randomTableB])-1 )

        # randomly select someone from the randomly chosen tables
        randomPersonA = self.repr[randomTableA][personAIndex]
        randomPersonB = self.repr[randomTableB][personBIndex]
        
        # add the randomly chosen person to the new table
        seatingNeighbor = deepcopy(self.repr)
        seatingNeighbor[randomTableA].append(randomPersonB)
        seatingNeighbor[randomTableB].append(randomPersonA)

        # remove the original ppl seated at the table
        seatingNeighbor[randomTableA].remove(randomPersonA)
        seatingNeighbor[randomTableB].remove(randomPersonB)

        # neighbors.append(Seating_RandomSwapNeighborhood_SA_Solution(repr=seatingNeighbor))

            # swaps -= 1

        return Seating_RandomSwapNeighborhood_SA_Solution(repr=seatingNeighbor)

In [ ]:
initial_solution = Seating_RandomSwapNeighborhood_SA_Solution()
best_solution = simulated_annealing(
    initial_solution, 
    maximization=True, 
    verbose=True, 
    max_iter=100,
    C=100.0,
    L=10,
    H=1.1)

print('Best solution', best_solution)

In [87]:
class Seating_SingleGreedyNeighborhood_SA_Solution(SeatingSolution):

    def _get_current_table(self, person):
        for table, guests in self.repr.items():
            if person in guests:
                return table
        return None  # if not found
    
    # This method must return a list of Solution objects (the neighbors)
    def get_random_neighbor(self):
        # this method swaps 2 random people from 2 random tables
        neighbor = None
        # swaps = 64
        randomTableA = randint(1, 8)
        personAIndex = randint(0, len(self.repr[randomTableA])-1 )
        personA = self.repr[randomTableA][personAIndex]
        # print("Person A: ", personA)

        # get only the people that the randomly chosen person has a relationship with
        filtered = df[df['idx'] == personA].iloc[0]
        filtered = filtered.drop('idx')
        peopleWithRelationship = [int(x) for x in filtered[filtered != 0].index] # convert to a list of numbers instead of strings like the Series would give
        # personB = max(peopleWithRelationship)

        # sort the lost from max to min
        peopleWithRelationship = sorted(peopleWithRelationship, reverse=True)
        # print("People with relationship: ", peopleWithRelationship)

        # print("negative 1: ", peopleWithRelationship[-1])

        for personB in peopleWithRelationship: 
            tableB = self._get_current_table(personB)

            if tableB == None:
                print("WARNING - table B not found")

            # only return the max person that is not already sharing a table
            if tableB == randomTableA:
                continue
            
            if personB == peopleWithRelationship[-1]:
                print("LAST ONE BUT SAME TABLE - ", personB)
                # add the randomly chosen person to the new table
                seatingNeighbor = deepcopy(self.repr)
                seatingNeighbor[randomTableA].append(personB)
                seatingNeighbor[tableB].append(personA)

                # remove the original ppl seated at the table
                seatingNeighbor[randomTableA].remove(personA)
                seatingNeighbor[tableB].remove(personB)

                neighbor = Seating_SingleGreedyNeighborhood_SA_Solution(repr=seatingNeighbor)
                break
            
            # add the randomly chosen person to the new table
            seatingNeighbor = deepcopy(self.repr)
            seatingNeighbor[randomTableA].append(personB)
            seatingNeighbor[tableB].append(personA)

            # remove the original ppl seated at the table
            seatingNeighbor[randomTableA].remove(personA)
            seatingNeighbor[tableB].remove(personB)

            neighbor = Seating_SingleGreedyNeighborhood_SA_Solution(repr=seatingNeighbor)
            break
            # neighbors.append(Seating_SingleGreedyNeighborhood_HillClimbingSolution(repr=seatingNeighbor))

        return neighbor

In [ ]:
# while True:
#     initial_solution = Seating_SingleGreedyNeighborhood_SA_Solution()
#     print("Initial Solution: ", initial_solution)
#     neighbor = initial_solution.get_random_neighbor()
#     print("Neighbor: ", neighbor.fitness())


In [82]:
initial_solution = Seating_SingleGreedyNeighborhood_SA_Solution()
best_solution = simulated_annealing(
    initial_solution, 
    maximization=True, 
    verbose=True, 
    max_iter=100,
    C=100.0,
    L=10,
    H=1.1)

print('Best solution', best_solution)
print('Best solution fitness', best_solution.fitness())

Initial solution: {1: [64, 16, 49, 36, 28, 21, 38, 53], 2: [51, 48, 29, 2, 37, 10, 17, 42], 3: [59, 50, 26, 25, 45, 11, 47, 9], 4: [3, 39, 20, 4, 23, 19, 54, 6], 5: [41, 32, 15, 40, 24, 62, 46, 22], 6: [1, 8, 14, 44, 60, 13, 58, 61], 7: [30, 63, 33, 27, 57, 5, 12, 7], 8: [55, 56, 31, 18, 52, 43, 34, 35]} with fitness 10100
Person A:  59
People with relationship:  [62, 61, 42, 1]
negative 1:  1
Random neighbor {1: [64, 16, 49, 36, 28, 21, 38, 53], 2: [51, 48, 29, 2, 37, 10, 17, 42], 3: [50, 26, 25, 45, 11, 47, 9, 62], 4: [3, 39, 20, 4, 23, 19, 54, 6], 5: [41, 32, 15, 40, 24, 46, 22, 59], 6: [1, 8, 14, 44, 60, 13, 58, 61], 7: [30, 63, 33, 27, 57, 5, 12, 7], 8: [55, 56, 31, 18, 52, 43, 34, 35]} with fitness: 10100
New current solution {1: [64, 16, 49, 36, 28, 21, 38, 53], 2: [51, 48, 29, 2, 37, 10, 17, 42], 3: [59, 50, 26, 25, 45, 11, 47, 9], 4: [3, 39, 20, 4, 23, 19, 54, 6], 5: [41, 32, 15, 40, 24, 62, 46, 22], 6: [1, 8, 14, 44, 60, 13, 58, 61], 7: [30, 63, 33, 27, 57, 5, 12, 7], 8: [55,

In [ ]:
# SA_fitnesses = []
# for _ in range(10):
#     initial_solution = Seating_SingleGreedyNeighborhood_SA_Solution()
#     best_solution = simulated_annealing(
#         initial_solution, 
#         maximization=True, 
#         verbose=False, 
#         max_iter=100,
#         C=100.0,
#         L=10,
#         H=1.1)

#     SA_fitnesses.append(best_solution.fitness())

# SA_fitnesses

In [106]:
class Seating_MultipleGreedyNeighborhood_SA_Solution(SeatingSolution):

    def _get_current_table(self, person):
        for table, guests in self.repr.items():
            if person in guests:
                return table
        return None  # if not found
    
    def get_random_neighbor(self):
        neighbors = []

        for _ in range(64): 
            randomTableA = randint(1, 8)
            personAIndex = randint(0, len(self.repr[randomTableA]) - 1)
            personA = self.repr[randomTableA][personAIndex]

            filtered = df[df['idx'] == personA].iloc[0]
            filtered = filtered.drop('idx')
            peopleWithRelationship = [int(x) for x in filtered[filtered != 0].index] 

            for personB in peopleWithRelationship:
                tableB = self._get_current_table(personB)

                if tableB == randomTableA:
                    continue

                if personB == peopleWithRelationship[-1] and len(neighbors) == 0:
                    seatingNeighbor = deepcopy(self.repr)

                    seatingNeighbor[randomTableA].append(personB)
                    seatingNeighbor[tableB].append(personA)

                    seatingNeighbor[randomTableA].remove(personA)
                    seatingNeighbor[tableB].remove(personB)

                    neighbors.append(Seating_MultipleGreedyNeighborhood_SA_Solution(repr=seatingNeighbor))

                seatingNeighbor = deepcopy(self.repr)

                seatingNeighbor[randomTableA].append(personB)
                seatingNeighbor[tableB].append(personA)

                seatingNeighbor[randomTableA].remove(personA)
                seatingNeighbor[tableB].remove(personB)

                neighbors.append(Seating_MultipleGreedyNeighborhood_SA_Solution(repr=seatingNeighbor))

        random_neighbor = randint(0, len(neighbors)-1)
        
        return neighbors[random_neighbor]

In [107]:
initial_solution = Seating_MultipleGreedyNeighborhood_SA_Solution()
best_solution = simulated_annealing(
    initial_solution, 
    maximization=True, 
    verbose=True, 
    max_iter=100,
    C=100.0,
    L=10,
    H=1.1)

print('Best solution', best_solution)

Initial solution: {1: [13, 56, 29, 61, 41, 15, 31, 46], 2: [59, 60, 53, 44, 9, 8, 21, 22], 3: [64, 25, 18, 49, 58, 10, 20, 45], 4: [51, 43, 27, 54, 6, 57, 48, 40], 5: [47, 4, 35, 3, 38, 30, 1, 23], 6: [12, 42, 62, 14, 32, 37, 33, 24], 7: [17, 28, 26, 34, 2, 11, 5, 50], 8: [36, 63, 52, 7, 39, 16, 19, 55]} with fitness 13100
Random neighbor {1: [13, 56, 29, 61, 41, 15, 31, 46], 2: [59, 60, 53, 44, 9, 8, 21, 22], 3: [64, 25, 18, 49, 58, 10, 45, 1], 4: [51, 43, 27, 54, 6, 57, 48, 40], 5: [47, 4, 35, 3, 38, 30, 23, 20], 6: [12, 42, 62, 14, 32, 37, 33, 24], 7: [17, 28, 26, 34, 2, 11, 5, 50], 8: [36, 63, 52, 7, 39, 16, 19, 55]} with fitness: 12400
Probability of accepting worse neighbor: 0.0009118819655545162
Neighbor is worse and was not accepted.
New current solution {1: [13, 56, 29, 61, 41, 15, 31, 46], 2: [59, 60, 53, 44, 9, 8, 21, 22], 3: [64, 25, 18, 49, 58, 10, 20, 45], 4: [51, 43, 27, 54, 6, 57, 48, 40], 5: [47, 4, 35, 3, 38, 30, 1, 23], 6: [12, 42, 62, 14, 32, 37, 33, 24], 7: [17, 28

In [108]:
# took an hour to run all 10 solutions
fitnessesSA = []
for _ in range(10):
    initial_solution = Seating_MultipleGreedyNeighborhood_SA_Solution()
    best_solution = simulated_annealing(
        initial_solution, 
        maximization=True, 
        verbose=True, 
        max_iter=100,
        C=100.0,
        L=10,
        H=1.1)
    fitnessesSA.append(best_solution.fitness())

Initial solution: {1: [46, 62, 39, 50, 25, 24, 54, 23], 2: [6, 5, 61, 49, 26, 40, 55, 59], 3: [31, 37, 35, 36, 34, 9, 15, 2], 4: [27, 58, 63, 44, 51, 48, 16, 32], 5: [14, 11, 3, 29, 13, 1, 41, 22], 6: [18, 7, 17, 12, 8, 45, 30, 60], 7: [20, 21, 10, 28, 64, 53, 19, 38], 8: [52, 33, 43, 4, 56, 47, 57, 42]} with fitness 17900
Random neighbor {1: [46, 62, 50, 25, 24, 54, 23, 34], 2: [6, 5, 61, 49, 26, 40, 55, 59], 3: [31, 37, 35, 36, 9, 15, 2, 39], 4: [27, 58, 63, 44, 51, 48, 16, 32], 5: [14, 11, 3, 29, 13, 1, 41, 22], 6: [18, 7, 17, 12, 8, 45, 30, 60], 7: [20, 21, 10, 28, 64, 53, 19, 38], 8: [52, 33, 43, 4, 56, 47, 57, 42]} with fitness: 17800
Probability of accepting worse neighbor: 0.36787944117144233
Neighbor is worse and was not accepted.
New current solution {1: [46, 62, 39, 50, 25, 24, 54, 23], 2: [6, 5, 61, 49, 26, 40, 55, 59], 3: [31, 37, 35, 36, 34, 9, 15, 2], 4: [27, 58, 63, 44, 51, 48, 16, 32], 5: [14, 11, 3, 29, 13, 1, 41, 22], 6: [18, 7, 17, 12, 8, 45, 30, 60], 7: [20, 21, 10

In [109]:
fitnessesSA

[42500, 36000, 35700, 31000, 37400, 39800, 34100, 33200, 37800, 37100]

In [110]:
# fitnessesSA = [42500, 36000, 35700, 31000, 37400, 39800, 34100, 33200, 37800, 37100]
avg_fitness = sum(fitnessesSA) / len(fitnessesSA)
print("Descriptions of the fitness for the multiple greedy hill climbing solution: ")
print("Average: ", int(avg_fitness))
print("Max: \t ", max(fitnessesSA))
print("Min: \t ", min(fitnessesSA))

Descriptions of the fitness for the multiple greedy hill climbing solution: 
Average:  36460
Max: 	  42500
Min: 	  31000


---